<font size="6" > <font color="DarkOrange">TensorFlow</font><font color="DarkGray">入門 2</font></font><font size="5" >  <font color="DarkSlateGray">: 2層ニューラルネットでのXOR論理の学習</font></font>

---

In [ ]:
import pandas as pd
from IPython.html import widgets

上の`import`はXORの表を描くためだけに使うものなので気にしないでください。pandasなどが入っていない場合は、ここと次の表の表示はスキップして<b><font color="DarkSlateGray">2. <strong><font color="DarkOrange">TensorFlow</font></strong>などの準備</font></b>から初めてください。

<b><font color="DarkSlateGray"><font size="4" >1. XORとは？</font></font></b>

XORの真理値表を思い出しましょう。表を描くために下を実行してみてください（コードに深い意味はありませんので気にしないでください）

In [ ]:
tab = pd.DataFrame([[0,1],[1,0]], columns=(0,1))
@widgets.interact
def f(s=(5, 30)):
    return (tab.style.background_gradient(cmap='spring').set_properties(**{'font-size': '{0}px'.format(s)}))

このように、例えば`[0,1]`を入れた時に`[1]`を出すようなXORニューラルネットを作りましょう。

<b><font color="DarkSlateGray"><font size="4" >2. <strong><font color="DarkOrange">TensorFlow</font></strong>などの準備</font></font></b>


---

まずは使うモジュールをimport

In [ ]:
import tensorflow as tf
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline

`inline`とすることで、有無を言わせずにノートブック上に図示させられます。

<b><font color="DarkSlateGray"><font size="4" >3. 訓練データを作る</font></font></b>

次に訓練データ( `4*2`配列 )とそのラベル( `4*1`配列 )を定義します:

In [ ]:
x_train = np.array([[0., 0.], [0.,1.], [1.,0.], [1.,1.]])
y_train = np.array([[0.],     [1.],    [1.],    [0.]])

Pythonは型を勝手に決めてくれるので、`float`となるように`0.`などと書きました。整数で書いて後から型変換しても構いません。

訓練データとラベルを入れるプレイスホルダーを用意します。今はデータは4点でもう決まっていますが、将来データが増えても良いようにわざわざプレイスホルダを作って、さらにデータ数は`None`で不定にしておきます。

In [ ]:
X = tf.placeholder(tf.float32, shape=[None, 2], name="X")
Y = tf.placeholder(tf.float32, shape=[None, 1], name="Y")

今回は中間層が一つのニューラルネットを使いましょう。中間層のユニット数を先に決めておきましょう:

In [ ]:
hidden_units = 4

お好きに変えても構いません。何も考えずにあまり増やすとまずいですが。。。

<b><font color="DarkSlateGray"><font size="4" >4. ニューラルネットを作る</font></font></b>

早速ニューラルネットの構築に移ります。

まずは第一層を定義しましょう:

In [ ]:
W1 = tf.Variable(tf.random_uniform([2, hidden_units], -1., 1.))
b1 = tf.Variable(tf.zeros([hidden_units]))
h = tf.nn.relu(tf.matmul(X, W1) + b1)


第二層も同様です:

In [ ]:
W2 = tf.Variable(tf.random_uniform([hidden_units, 1], -1., 1.))
b2 = tf.Variable(tf.zeros([1]))
y_model = tf.nn.sigmoid(tf.matmul(h, W2) + b2)

<b><font color="DarkSlateGray"><font size="4" >5. 訓練の詳細を設定</font></font></b>

次は誤差関数と`optimizer`の選択です。二乗誤差に対して`Adam`勾配法を用いてみましょう。

In [ ]:
loss = tf.reduce_mean(tf.square(y_model - y_train))

optimizer = tf.train.AdamOptimizer(0.05)

train = optimizer.minimize(loss)

`reduce_mean`は配列の全成分にわたる平均値です。`reduce_`ほにゃららはよく使うので、成分にわたる操作に注意を払ってください。

<b><font color="DarkSlateGray"><font size="4" >6. 訓練</font></font></b>


まず、空のプレイスホルダー`X, Y`に、`x_train, y_train`の値を渡す操作を定めておきます。後で`Session`の中で渡しても構いません。

In [ ]:
feed_dict = {X: x_train, Y: y_train}

`Session`にもあだ名をつけておきます。

In [ ]:
sess = tf.Session()

さて、訓練のステップ数を適当に決めておきます。ここでは余裕を持って`3000`くらいにしてみましょう。

In [ ]:
Epochs = 3000

以上で全ての設定が終わりました。いよいよ訓練に移るので、まずは全`Variables`を初期化しておきましょう。

In [ ]:
init = tf.global_variables_initializer()
sess.run(init)

ではステップ数`Epochs`だけ、勾配降下法で学習させてみましょう。途中経過を見るために200ステップ置きに訓練誤差の値を表示させておきます。

(initializerをはしらせなければ、下のステップを繰り返すたびに追加でさらに200ステップづつ訓練させられます)

In [ ]:
for epoch in range(Epochs):
    _, l, output = sess.run([train, loss, y_model], feed_dict=feed_dict)
    if epoch % 200 == 0:
        print('Step: ', epoch)
        print('Current error value: ', l)
print('END')

さてどれくらいXORが再現できるようになったでしょうか？学習済みモデルのaccuracyと、それに`[0,0], [1,0], [0,1], [1,1]`を入力した時の出力値を表示しましょう。

In [ ]:
model = 1. - abs(Y - y_model) 
accuracy = tf.reduce_mean(model)
#今のXORの場合は、訓練データ4点がありうるデータの全てなので、それらがテストデータでもある。従ってその上で評価する。
y_out, acry = sess.run([y_model, accuracy], feed_dict=feed_dict)

print('Model accuracy is', acry)
print('Outputs are\n', y_out)

さて精度はどうだったでしょう？local minimaにはまってしまいましたか？うまくいきましたか？

初期化からまた実行し直すことで、再び学習をやり直せます。すると数回に一度はlocal minimumにハマるのが実感できるかと思います。

分類境界付近の点を大量に生成させてプロットしてみましょう。

In [ ]:
plt.figure()

x_scatter = np.random.rand(10**6, 2)*3.4 - 1.3
y_scatter = sess.run(y_model, feed_dict={X: x_scatter})
border = np.where(np.logical_and(0.498<y_scatter, y_scatter<0.502))[0]
Ind_scatter = x_scatter[border]
sep = plt.scatter(Ind_scatter[:,0], Ind_scatter[:,1], marker='o', color='orange', s=1.5)

y_1 = plt.scatter([1,0], [0,1], marker='^', color='red', s=100)
y_0 = plt.scatter([1,0], [1,0], marker='v', color='gray', s=100)

plt.legend((sep, y_1, y_0),('Bndy', '1', '0'),  scatterpoints=1)
plt.show()

ちなみに初期化して、そのすぐ次にこのプロットをすると、初期値パラメータでのモデルの振る舞いが見て取れます。ランダム初期値ではモデルは全くひどい振る舞いであることがわかり、数千ステップでの勾配法の成果が体感できます。

また、初期値の悪さと学習後にモデルが到達できる状態をプロットとして見比べるのも示唆に富みます。色々試してみてください。本格的な深層学習になると、初期値のランダムサンプリングの仕方が学習の結果に大きく影響します（He's initialization等）。

<b><font color="DarkSlateGray"><font size="4" >7. おまけ：ドロップアウト</font></font></b>

コピペ反復コードはとても良くないですが、話の流れ上、さっきのコードの一部を改めてここにそのままコピーして、中間層にドロップアウトを入れましょう。

In [ ]:
W1_2 = tf.Variable(tf.random_uniform([2, 4], -1., 1.))
b1_2 = tf.Variable(tf.zeros([4]))
h_2 = tf.nn.relu(tf.matmul(X, W1_2) + b1_2)
keep_prob = tf.placeholder(tf.float32)
hd_2 = tf.nn.dropout(h_2, keep_prob)

W2_2 = tf.Variable(tf.random_uniform([4, 1], -1., 1.))
b2_2 = tf.Variable(tf.zeros([1]))
y_model_2 = tf.nn.sigmoid(tf.matmul(hd_2, W2_2) + b2_2)

loss_2 = tf.reduce_mean(tf.square(y_model_2 - y_train))
train_2 = optimizer.minimize(loss_2)

走らせてみましょう。

In [ ]:
init = tf.global_variables_initializer()
sess.run(init)

for epoch in range(1800):
    _, l, output = sess.run([train_2, loss_2, y_model_2], feed_dict={X: x_train, Y: y_train, keep_prob: 0.5})
    if epoch % 200 == 0:
        print('Step: ', epoch)
        print('Current error value: ', l)
print('END')

In [ ]:
model2 = 1. - abs(Y - y_model_2)
accuracy2 = tf.reduce_mean(model2)
y_out2, acry2 = sess.run([y_model_2, accuracy2], feed_dict={X: x_train, Y: y_train, keep_prob: 1.0})

print('Model accuracy is', acry2)
print('Outputs are\n', y_out2)

モデルもデータサイズも貧弱な例なのでいまいち精度は... 

それもそのはず、たった4個しかない中間層のユニットを間引いてしまっては弱小モデルしかできません。アンサンブル効果を狙うドロップアウトですが、ダメすぎのモデルをいくら集めても全く効果は期待できません（ポートフォリオを作ってモデルの予測安定性を実現するのがアンサンブル法です）。したがってドロップアウトが有効なのは、大きなニューラルネットの場合です（ドロップアウトについてちゃんと理解したいなら、Goodfellowらの"Deep Learning"と関連論文必読）。

<b><font color="DarkSlateGray"><font size="4" >8. おまけ2：ドロップアウトがうまくいくとき</font></font></b>

先ほどはモデルが小さすぎてドロップアウトが逆効果でした。そこで中間層を10ユニットに増やしてドロップアウトしてみましょう。ちょっと間抜けですが、モデルから実行までを改めて全部書いてしまうと

In [ ]:
W1_3 = tf.Variable(tf.random_uniform([2, 10], -1., 1.))
b1_3 = tf.Variable(tf.zeros([10]))
h_3 = tf.nn.relu(tf.matmul(X, W1_3) + b1_3)
keep_prob = tf.placeholder(tf.float32)
hd_3 = tf.nn.dropout(h_3, keep_prob)

W2_3 = tf.Variable(tf.random_uniform([10, 1], -1., 1.))
b2_3 = tf.Variable(tf.zeros([1]))
y_model_3 = tf.nn.sigmoid(tf.matmul(hd_3, W2_3) + b2_3)

loss_3 = tf.reduce_mean(tf.square(y_model_3 - y_train))
train3 = optimizer.minimize(loss_3)

init = tf.global_variables_initializer()
sess.run(init)

for epoch in range(1800):
    _, l, output = sess.run([train3, loss_3, y_model_3], feed_dict={X: x_train, Y: y_train, keep_prob: 0.4})
    if epoch % 200 == 0:
        print('Step: ', epoch)
        print('Current error value: ', l)
print('END')

In [ ]:
model3 = 1. - abs(Y - y_model_3)
accuracy3 = tf.reduce_mean(model3)
y_out3, acry3 = sess.run([y_model_3, accuracy3], feed_dict={X: x_train, Y: y_train, keep_prob: 1.0})

print('Model accuracy is', acry3)
print('Outputs are\n', y_out3)

どうでしょう？学習結果の振れ幅が小さくなり、だいぶ安定しましたね！（その代わりaccuracyが0.99となることも無くなりましたが。）これは中間層が10ノードのネットワークをドロップアウト率0.6で間引くことで、元と同じ4ノードのネットワークのアンサンブルが仮想的に得られているからです。

以上、学習ステップ数やノード数、ドロップアウト率などのハイパーパラメータは最適化していないので、皆さんで色々調整してさらに精度を上げてみてください。あるいは`optimizer`や活性化関数、正則化も色々と変えられます。

簡単なおもちゃモデルですが、様々な深層学習の技法を理解するのには役に立ちます。色々な深層学習のテクニックも、理屈をきちんと考えて使わないと意味がないことが学べると思います。